<h1>10. NetCDF I/O</h1>
<h2>10/25/2023</h2>

<h2>10.0 Last Time...</h2>
<ul>
    <li>Statistics that are not resistant to outliers include the mean, the standard deviation, skewness, and kurtosis.</li>
    <li>Statistics that are resistant to outliers include the median and the interquartile range.</li>
    <li>By making use of dictionaries, we can create versatile, non-hard-coded programs!</li>
    <li>glob is a package that enables us to grab all files within a directory</li>
</ul>

<h2>10.1 Structure of a NetCDF File</h2>

NetCDF is a commonly used file format in our field because it enables the storage of data as well as the storage of its <b>metadata</b>. Every major language in our field is equipped to deal with NetCDF files, and Python is no exception!

There are <b>four</b> parameter types in a netCDF file:
<ul>
    <li><b>Global attributes:</b> strings that describe the file as a whole: for example, a title, who created it, what standards it follows.</li>
    <li><b>Variables:</b> entities that hold data, which includes the data, the domain the data is defined on (dimensionality), and metadata about the data (for example, units).</li>
    <li><b>Variable attributes:</b> actual storage of the data's metadata.</li>
    <li><b>Dimensions:</b> not only define the domain, but also might have values of their own (for example, latitude values, longitude values, altitude values, etc.).</li>
</ul>

As an example, you might have a timeseries of surface temperature for a latitude-longitude grid. The dimensions for that dataset would be <b>lat</b>, <b>lon</b>, and <b>time</b>. The variable <b>lat</b> would just tell you the number of elements in the <b>lat</b> dimension</b>; likewise for <b>lon</b> and <b>time</b>. Finally, you might have a variable containing temperatures called <b>Ts</b> that would be 3-D, with dimensions of <b>lat</b>, <b>lon</b>, and <b>time</b>.

There are several packages that can read NetCDF files; we're going to learn SciPy today - it's not necessarily the best, but it is one of the easiest to learn, and SciPy is a useful package for many other reasons.

<h2>10.2 Reading a NetCDF File</h2>

For NetCDF files, we're interested in the I/O functionality of SciPy, so we'll call that part of the package and assign it to an alias.

In [2]:
# Import the I/O functionality of SciPy.
import numpy as np
import scipy.io as S



To create a file object, it's actually a pretty similar approach to what we did in our I/O lecture.

In [4]:
# Read in the provided NetCDF file in read-only mode.
fileobj = S.netcdf_file("../datasets/air.mon.mean.nc", mode="r")
print(fileobj)


NetCDF file objects have several <b>attributes</b> that we can call on (more on this when we explore object-oriented programming). One of those attributes is called <b>variables</b>, which is a dictionary. The keys of the dictionary are strings corresponding to the names of the variables, and the values are a special kind of object called <b>variable objects</b> that contain the variable's values as well as any metadata (units, etc.).

Another NetCDF file object attribute is <b>dimensions</b>, which is another dictionary. The keys of this dictionary are strings that are the names of the dimensions, and the values are the lengths of the dimensions.

Let's see an example from our .nc file: a grid of monthly-mean temperature values.

In [5]:
# Let's import NumPy and SciPy's I/O functionality.
fileobj = S.netcdf_file("../datasets/air.mon.mean.nc", mode="r")


# Now, create a file object!



# First, let's find out what information's in the title.
print(fileobj.title)


b'Monthly mean air temperature NCEP Reanalysis'


In [6]:
# Now let's explore the dimensions dictionary.
print(fileobj.dimensions)

# Time is set to 'None' because that's this file's
# 'unlimited' dimension; you can keep adding new times to it
# and it will use the same lat/lon grid.

{'lon': 144, 'lat': 73, 'time': None}


In [7]:
# And let's see what kinds of variables are inside.
print(fileobj.variables)


{'lat': <scipy.io._netcdf.netcdf_variable object at 0x7f19fffc28d0>, 'lon': <scipy.io._netcdf.netcdf_variable object at 0x7f19fffc3450>, 'time': <scipy.io._netcdf.netcdf_variable object at 0x7f19fffc1f50>, 'air': <scipy.io._netcdf.netcdf_variable object at 0x7f19fffc1bd0>}


In [9]:
# Okay, that's all very messy!
# Now it's time to grab the values of air temperature.

temp = fileobj.variables["air"]
print(temp)

In [10]:
# We can now examine this data more carefully.
print(temp.units)
print(temp.shape)
print(temp[:])


b'degC'
(755, 73, 144)
[[[-34.926773  -34.926773  -34.926773  ... -34.926773  -34.926773
   -34.926773 ]
  [-35.13935   -35.129673  -35.12742   ... -35.188705  -35.170002
   -35.14935  ]
  [-34.352573  -34.04226   -33.768707  ... -35.333866  -35.002903
   -34.671288 ]
  ...
  [-16.525156  -16.404509  -16.284832  ... -16.795155  -16.737736
   -16.643543 ]
  [-16.190313  -16.202248  -16.21677   ... -16.132574  -16.161928
   -16.178377 ]
  [-17.697733  -17.697733  -17.697733  ... -17.697733  -17.697733
   -17.697733 ]]

 [[-33.311375  -33.311375  -33.311375  ... -33.311375  -33.311375
   -33.311375 ]
  [-34.65034   -34.476204  -34.29689   ... -35.18448   -35.009308
   -34.835514 ]
  [-34.1031    -33.619995  -33.161373  ... -35.606552  -35.103443
   -34.602757 ]
  ...
  [-34.338963  -34.21862   -34.08241   ... -34.359997  -34.42724
   -34.418617 ]
  [-33.795513  -33.896553  -33.977238  ... -33.41517   -33.56758
   -33.690342 ]
  [-32.942413  -32.942413  -32.942413  ... -32.942413  -32.9424

In [11]:
# Let's be a little more restrained... how about all the data at the first lat/lon pair?
print(temp[0,0,0])


-34.926773


In [12]:
# That seems pretty chilly! What are the lat/lon values?
lat = fileobj.variables["lat"]
lon = fileobj.variables["lon"]

print(lat[0])
print(lon[0])



90.0
0.0


In [ ]:
# Okay, that's reasonable for the North Pole.
# This grid is 2.5 degrees... let's find out what Seattle's weather was like!

# Seattle is at approximately 47.5 N and 122.5 W.

# This dataset's lon starts at 0 and counts up to 360.
# So 122.25 W corresponds to 360-122.5 = 237.5.

# Remember, lat and lon are those weird data types:


In [13]:
# So let's save their values instead.
a = lat[:]
b = lon[:]
print(a)
print(b)

[ 90.   87.5  85.   82.5  80.   77.5  75.   72.5  70.   67.5  65.   62.5
  60.   57.5  55.   52.5  50.   47.5  45.   42.5  40.   37.5  35.   32.5
  30.   27.5  25.   22.5  20.   17.5  15.   12.5  10.    7.5   5.    2.5
   0.   -2.5  -5.   -7.5 -10.  -12.5 -15.  -17.5 -20.  -22.5 -25.  -27.5
 -30.  -32.5 -35.  -37.5 -40.  -42.5 -45.  -47.5 -50.  -52.5 -55.  -57.5
 -60.  -62.5 -65.  -67.5 -70.  -72.5 -75.  -77.5 -80.  -82.5 -85.  -87.5
 -90. ]
[  0.    2.5   5.    7.5  10.   12.5  15.   17.5  20.   22.5  25.   27.5
  30.   32.5  35.   37.5  40.   42.5  45.   47.5  50.   52.5  55.   57.5
  60.   62.5  65.   67.5  70.   72.5  75.   77.5  80.   82.5  85.   87.5
  90.   92.5  95.   97.5 100.  102.5 105.  107.5 110.  112.5 115.  117.5
 120.  122.5 125.  127.5 130.  132.5 135.  137.5 140.  142.5 145.  147.5
 150.  152.5 155.  157.5 160.  162.5 165.  167.5 170.  172.5 175.  177.5
 180.  182.5 185.  187.5 190.  192.5 195.  197.5 200.  202.5 205.  207.5
 210.  212.5 215.  217.5 220.  222.5 225.  

In [17]:
# Now we can use np.where() to find the locations of the values in the dataset.
sealat = np.where(a == 47.5)
sealon = np.where(b == 237.5)

print(sealat)
print(sealon)

(array([17]),)
(array([95]),)


In [18]:
# Let's print it out!
print(temp[0,sealat, sealon])


[[1.5006493]]


In [19]:
# If you want the full name of a particular variable, long_name is useful!
print(fileobj.variables["air"].long_name)



b'Monthly Mean Air Temperature'


<h2>10.3 Writing a NetCDF File</h2>

Just as with normal files, we can write our own NetCDF files!

You can create a NetCDF file object in write mode!

In [21]:
newfile = S.netcdf_file("new.nc",mode="w")

# Let's start by putting in 10 latitude and 20 longitude values.
lat = np.arange(10)
lon = np.arange(10)

# And maybe two different sets of data, one array and one scalar.
data1 = np.reshape(np.sin(np.arange(200)*0.1),(10,20))
data2 = 42.0

print(data1)
print(data2)

[[ 0.          0.09983342  0.19866933  0.29552021  0.38941834  0.47942554
   0.56464247  0.64421769  0.71735609  0.78332691  0.84147098  0.89120736
   0.93203909  0.96355819  0.98544973  0.99749499  0.9995736   0.99166481
   0.97384763  0.94630009]
 [ 0.90929743  0.86320937  0.8084964   0.74570521  0.67546318  0.59847214
   0.51550137  0.42737988  0.33498815  0.23924933  0.14112001  0.04158066
  -0.05837414 -0.15774569 -0.2555411  -0.35078323 -0.44252044 -0.52983614
  -0.61185789 -0.68776616]
 [-0.7568025  -0.81827711 -0.87157577 -0.91616594 -0.95160207 -0.97753012
  -0.993691   -0.99992326 -0.99616461 -0.98245261 -0.95892427 -0.92581468
  -0.88345466 -0.83226744 -0.77276449 -0.70554033 -0.63126664 -0.55068554
  -0.46460218 -0.37387666]
 [-0.2794155  -0.1821625  -0.0830894   0.0168139   0.1165492   0.21511999
   0.31154136  0.40484992  0.49411335  0.57843976  0.6569866   0.72896904
   0.79366786  0.85043662  0.8987081   0.93799998  0.96791967  0.98816823
   0.99854335  0.99894134]
 [ 0

In [23]:
# So far so good! Let's create the actual dimension information.
newfile.createDimension("lat",len(lat))
newfile.createDimension("lon",len(lon))


In [ ]:
# Now the names of our variables!



In [ ]:
# And now we assign the actual values to our variables!


In [ ]:
# And assign some units!


In [ ]:
# Add a title to finish up!


Okay, so having done all that (don't worry if all the details are unclear - this is a fairly advanced topic that will take some practice!), let's try reading our values.

<h2>10.4 NetCDF Example</h2>

Let's pull up some monthly mean surface air temperature data from our air.mon.mean.nc data file. These data come from the NCEP/NCAR Reanalysis 1.

In [ ]:

# Let's take a look at the time units.


In [ ]:
# Well, that seems confusing.
# Let's create a new version of the file where time just starts at 0.0, and change the units string so it just says 'hours'.


In [ ]:
# And let's test it!



<h2>10.5 Take-Home Points</h2>
<ul>
    <li>NetCDF is a powerful file type containing global attributes, variables, variable attributes, and dimensions.</li>
    <li>We can read from NetCDF files using similar syntax to that for regular files.</li>
    <li>Using attributes such as 'dimensions' and 'variables', we can learn about individual variables in the dataset.</li>
    <li>We can also write to NetCDF files in a simlar way.</li>
</ul>